In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [3]:
# Convolutional neural network (two convolutional layers)
class BiLSTM_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(BiLSTM_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.lstm = nn.LSTM(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(512, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.lstm(x)
        #b,64,256
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,256 * b,64,1 = b,64,256
        x = torch.sum(x,dim=1)
        #b,64,256 -> b,,256
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [4]:
test = BiLSTM_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.25 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\functional.py:1795: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")


torch.Size([10, 4])

In [5]:
writer = SummaryWriter()

In [6]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [7]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [8]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [9]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [10]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [11]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [12]:
model = BiLSTM_AT(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 28.1250%, Training Loss: 1.4554%
Epoch [1/300], Step [2/225], Training Accuracy: 23.4375%, Training Loss: 1.4959%
Epoch [1/300], Step [3/225], Training Accuracy: 24.4792%, Training Loss: 1.4809%
Epoch [1/300], Step [4/225], Training Accuracy: 25.3906%, Training Loss: 1.4844%
Epoch [1/300], Step [5/225], Training Accuracy: 28.1250%, Training Loss: 1.4544%
Epoch [1/300], Step [6/225], Training Accuracy: 26.8229%, Training Loss: 1.4805%
Epoch [1/300], Step [7/225], Training Accuracy: 26.7857%, Training Loss: 1.4842%
Epoch [1/300], Step [8/225], Training Accuracy: 27.7344%, Training Loss: 1.4824%
Epoch [1/300], Step [9/225], Training Accuracy: 27.9514%, Training Loss: 1.4880%
Epoch [1/300], Step [10/225], Training Accuracy: 26.7188%, Training Loss: 1.4976%
Epoch [1/300], Step [11/225], Training Accuracy: 26.9886%, Training Loss: 1.4938%
Epoch [1/300], Step [12/225], Training Accuracy: 26.8229%, Training Loss: 1.4906%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [111/225], Training Accuracy: 28.9837%, Training Loss: 1.3993%
Epoch [1/300], Step [112/225], Training Accuracy: 29.0039%, Training Loss: 1.3981%
Epoch [1/300], Step [113/225], Training Accuracy: 28.9270%, Training Loss: 1.3985%
Epoch [1/300], Step [114/225], Training Accuracy: 29.0433%, Training Loss: 1.3972%
Epoch [1/300], Step [115/225], Training Accuracy: 29.0625%, Training Loss: 1.3967%
Epoch [1/300], Step [116/225], Training Accuracy: 29.1218%, Training Loss: 1.3963%
Epoch [1/300], Step [117/225], Training Accuracy: 29.1533%, Training Loss: 1.3964%
Epoch [1/300], Step [118/225], Training Accuracy: 29.1976%, Training Loss: 1.3961%
Epoch [1/300], Step [119/225], Training Accuracy: 29.1886%, Training Loss: 1.3959%
Epoch [1/300], Step [120/225], Training Accuracy: 29.1667%, Training Loss: 1.3958%
Epoch [1/300], Step [121/225], Training Accuracy: 29.1968%, Training Loss: 1.3955%
Epoch [1/300], Step [122/225], Training Accuracy: 29.1368%, Training Loss: 1.3956%
Epoc

Epoch [2/300], Step [2/225], Training Accuracy: 35.9375%, Training Loss: 1.3001%
Epoch [2/300], Step [3/225], Training Accuracy: 33.3333%, Training Loss: 1.3225%
Epoch [2/300], Step [4/225], Training Accuracy: 34.3750%, Training Loss: 1.3087%
Epoch [2/300], Step [5/225], Training Accuracy: 33.7500%, Training Loss: 1.3076%
Epoch [2/300], Step [6/225], Training Accuracy: 32.8125%, Training Loss: 1.3197%
Epoch [2/300], Step [7/225], Training Accuracy: 32.8125%, Training Loss: 1.3163%
Epoch [2/300], Step [8/225], Training Accuracy: 34.5703%, Training Loss: 1.3019%
Epoch [2/300], Step [9/225], Training Accuracy: 34.8958%, Training Loss: 1.3038%
Epoch [2/300], Step [10/225], Training Accuracy: 35.3125%, Training Loss: 1.2974%
Epoch [2/300], Step [11/225], Training Accuracy: 34.6591%, Training Loss: 1.2975%
Epoch [2/300], Step [12/225], Training Accuracy: 34.2448%, Training Loss: 1.2941%
Epoch [2/300], Step [13/225], Training Accuracy: 34.1346%, Training Loss: 1.2960%
Epoch [2/300], Step [14/

Epoch [2/300], Step [106/225], Training Accuracy: 36.3060%, Training Loss: 1.2825%
Epoch [2/300], Step [107/225], Training Accuracy: 36.2734%, Training Loss: 1.2825%
Epoch [2/300], Step [108/225], Training Accuracy: 36.2992%, Training Loss: 1.2825%
Epoch [2/300], Step [109/225], Training Accuracy: 36.1955%, Training Loss: 1.2826%
Epoch [2/300], Step [110/225], Training Accuracy: 36.2926%, Training Loss: 1.2816%
Epoch [2/300], Step [111/225], Training Accuracy: 36.2050%, Training Loss: 1.2818%
Epoch [2/300], Step [112/225], Training Accuracy: 36.2305%, Training Loss: 1.2813%
Epoch [2/300], Step [113/225], Training Accuracy: 36.1587%, Training Loss: 1.2825%
Epoch [2/300], Step [114/225], Training Accuracy: 36.2253%, Training Loss: 1.2815%
Epoch [2/300], Step [115/225], Training Accuracy: 36.1821%, Training Loss: 1.2812%
Epoch [2/300], Step [116/225], Training Accuracy: 36.2338%, Training Loss: 1.2806%
Epoch [2/300], Step [117/225], Training Accuracy: 36.1245%, Training Loss: 1.2818%
Epoc

Epoch [2/300], Step [224/225], Training Accuracy: 37.2001%, Training Loss: 1.2659%
Epoch [2/300], Step [225/225], Training Accuracy: 37.2360%, Training Loss: 1.2658%
Epoch [3/300], Step [1/225], Training Accuracy: 31.2500%, Training Loss: 1.2134%
Epoch [3/300], Step [2/225], Training Accuracy: 30.4688%, Training Loss: 1.2586%
Epoch [3/300], Step [3/225], Training Accuracy: 29.1667%, Training Loss: 1.2929%
Epoch [3/300], Step [4/225], Training Accuracy: 29.2969%, Training Loss: 1.2734%
Epoch [3/300], Step [5/225], Training Accuracy: 31.8750%, Training Loss: 1.2641%
Epoch [3/300], Step [6/225], Training Accuracy: 32.5521%, Training Loss: 1.2635%
Epoch [3/300], Step [7/225], Training Accuracy: 33.4821%, Training Loss: 1.2615%
Epoch [3/300], Step [8/225], Training Accuracy: 35.1562%, Training Loss: 1.2506%
Epoch [3/300], Step [9/225], Training Accuracy: 35.5903%, Training Loss: 1.2499%
Epoch [3/300], Step [10/225], Training Accuracy: 36.0938%, Training Loss: 1.2384%
Epoch [3/300], Step [11

...

Epoch [298/300], Step [158/225], Training Accuracy: 99.5649%, Training Loss: 0.0201%
Epoch [298/300], Step [159/225], Training Accuracy: 99.5578%, Training Loss: 0.0203%
Epoch [298/300], Step [160/225], Training Accuracy: 99.5605%, Training Loss: 0.0202%
Epoch [298/300], Step [161/225], Training Accuracy: 99.5633%, Training Loss: 0.0201%
Epoch [298/300], Step [162/225], Training Accuracy: 99.5660%, Training Loss: 0.0200%
Epoch [298/300], Step [163/225], Training Accuracy: 99.5686%, Training Loss: 0.0201%
Epoch [298/300], Step [164/225], Training Accuracy: 99.5713%, Training Loss: 0.0200%
Epoch [298/300], Step [165/225], Training Accuracy: 99.5644%, Training Loss: 0.0201%
Epoch [298/300], Step [166/225], Training Accuracy: 99.5576%, Training Loss: 0.0201%
Epoch [298/300], Step [167/225], Training Accuracy: 99.5603%, Training Loss: 0.0201%
Epoch [298/300], Step [168/225], Training Accuracy: 99.5629%, Training Loss: 0.0201%
Epoch [298/300], Step [169/225], Training Accuracy: 99.5655%, Tra

Epoch [299/300], Step [47/225], Training Accuracy: 99.7008%, Training Loss: 0.0175%
Epoch [299/300], Step [48/225], Training Accuracy: 99.7070%, Training Loss: 0.0173%
Epoch [299/300], Step [49/225], Training Accuracy: 99.7130%, Training Loss: 0.0172%
Epoch [299/300], Step [50/225], Training Accuracy: 99.7188%, Training Loss: 0.0171%
Epoch [299/300], Step [51/225], Training Accuracy: 99.6936%, Training Loss: 0.0172%
Epoch [299/300], Step [52/225], Training Accuracy: 99.6995%, Training Loss: 0.0172%
Epoch [299/300], Step [53/225], Training Accuracy: 99.7052%, Training Loss: 0.0174%
Epoch [299/300], Step [54/225], Training Accuracy: 99.7106%, Training Loss: 0.0173%
Epoch [299/300], Step [55/225], Training Accuracy: 99.7159%, Training Loss: 0.0171%
Epoch [299/300], Step [56/225], Training Accuracy: 99.7210%, Training Loss: 0.0172%
Epoch [299/300], Step [57/225], Training Accuracy: 99.7259%, Training Loss: 0.0172%
Epoch [299/300], Step [58/225], Training Accuracy: 99.7306%, Training Loss: 

Epoch [299/300], Step [145/225], Training Accuracy: 99.7306%, Training Loss: 0.0179%
Epoch [299/300], Step [146/225], Training Accuracy: 99.7217%, Training Loss: 0.0179%
Epoch [299/300], Step [147/225], Training Accuracy: 99.7236%, Training Loss: 0.0179%
Epoch [299/300], Step [148/225], Training Accuracy: 99.7255%, Training Loss: 0.0179%
Epoch [299/300], Step [149/225], Training Accuracy: 99.7169%, Training Loss: 0.0180%
Epoch [299/300], Step [150/225], Training Accuracy: 99.7188%, Training Loss: 0.0180%
Epoch [299/300], Step [151/225], Training Accuracy: 99.7206%, Training Loss: 0.0179%
Epoch [299/300], Step [152/225], Training Accuracy: 99.7225%, Training Loss: 0.0180%
Epoch [299/300], Step [153/225], Training Accuracy: 99.7243%, Training Loss: 0.0179%
Epoch [299/300], Step [154/225], Training Accuracy: 99.7159%, Training Loss: 0.0179%
Epoch [299/300], Step [155/225], Training Accuracy: 99.7177%, Training Loss: 0.0179%
Epoch [299/300], Step [156/225], Training Accuracy: 99.7095%, Tra

Epoch [300/300], Step [35/225], Training Accuracy: 99.7321%, Training Loss: 0.0165%
Epoch [300/300], Step [36/225], Training Accuracy: 99.6962%, Training Loss: 0.0169%
Epoch [300/300], Step [37/225], Training Accuracy: 99.7044%, Training Loss: 0.0169%
Epoch [300/300], Step [38/225], Training Accuracy: 99.7122%, Training Loss: 0.0167%
Epoch [300/300], Step [39/225], Training Accuracy: 99.7196%, Training Loss: 0.0165%
Epoch [300/300], Step [40/225], Training Accuracy: 99.7266%, Training Loss: 0.0164%
Epoch [300/300], Step [41/225], Training Accuracy: 99.7332%, Training Loss: 0.0162%
Epoch [300/300], Step [42/225], Training Accuracy: 99.7396%, Training Loss: 0.0162%
Epoch [300/300], Step [43/225], Training Accuracy: 99.7456%, Training Loss: 0.0161%
Epoch [300/300], Step [44/225], Training Accuracy: 99.7514%, Training Loss: 0.0161%
Epoch [300/300], Step [45/225], Training Accuracy: 99.7569%, Training Loss: 0.0159%
Epoch [300/300], Step [46/225], Training Accuracy: 99.7622%, Training Loss: 

Epoch [300/300], Step [137/225], Training Accuracy: 99.6122%, Training Loss: 0.0189%
Epoch [300/300], Step [138/225], Training Accuracy: 99.6037%, Training Loss: 0.0191%
Epoch [300/300], Step [139/225], Training Accuracy: 99.6066%, Training Loss: 0.0190%
Epoch [300/300], Step [140/225], Training Accuracy: 99.5982%, Training Loss: 0.0190%
Epoch [300/300], Step [141/225], Training Accuracy: 99.6011%, Training Loss: 0.0189%
Epoch [300/300], Step [142/225], Training Accuracy: 99.6039%, Training Loss: 0.0190%
Epoch [300/300], Step [143/225], Training Accuracy: 99.6066%, Training Loss: 0.0190%
Epoch [300/300], Step [144/225], Training Accuracy: 99.6094%, Training Loss: 0.0190%
Epoch [300/300], Step [145/225], Training Accuracy: 99.6121%, Training Loss: 0.0190%
Epoch [300/300], Step [146/225], Training Accuracy: 99.6147%, Training Loss: 0.0190%
Epoch [300/300], Step [147/225], Training Accuracy: 99.6067%, Training Loss: 0.0190%
Epoch [300/300], Step [148/225], Training Accuracy: 99.6094%, Tra

In [15]:
from playsound import playsound
playsound(u"sound.mp3")

In [16]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 44.3023902167871 %
